In [44]:
import lmdb
import pickle
import glob
import os
import pandas as pd
from torch_geometric.data import Data

In [45]:
def extract_dataset(path):
    all_data = []
    lmdb_files = sorted(glob.glob(os.path.join(path, "data.*.lmdb")))
    
    # all the properties available in the metadata pickle file
    columns = [
        "sid",
        "y_relaxed",
        "bulk_id",
        "bulk_symbols",
        "miller_index",
        "traj_id",
        "slab_sid",
        "ads_symbols",
        "nads"
    ]

    print(f"num of files: {len(lmdb_files)}")

    with open("oc22_metadata.pkl", "rb") as f:
        metadata = pickle.load(f)

    for file in lmdb_files:
        env = lmdb.open(file, readonly=True, subdir=False, lock=False)

        with env.begin() as txn:
            print(txn.stat())
            num_entries = txn.stat()['entries']
            print(f"Processing {file}: {num_entries} entries")
            cursor = txn.cursor()
            for key, value in cursor:
                try:
                    # load pytorch data obj manually due to the imcompatible PyG version of OC22 dataset
                    data = Data.from_dict(pickle.loads(value).__dict__)
                    print(data)
                    sid = data.sid
                    y_relaxed = data.y_relaxed

                    row = {
                        "sid": sid,
                        "y_relaxed": y_relaxed
                    }

                    if sid in metadata:
                        row.update(metadata[sid])

                    all_data.append(row)
                except Exception as e:
                    print(f"{e}")
            
    env.close()

    return pd.DataFrame(all_data, columns=columns)

In [46]:
train_path = "oc22/is2re-total/train"
val_id_path = "oc22/is2re-total/val_id"
val_ood_path = "oc22/is2re-total/val_ood"

train = extract_dataset(train_path)
val_id = extract_dataset(val_id_path)
val_ood = extract_dataset(val_ood_path)

train.to_csv("data/train.csv", index=False)
val_id.to_csv("data/val_id.csv", index=False)
val_ood.to_csv("data/val_ood.csv", index=False)

num of files: 41
{'psize': 4096, 'depth': 2, 'branch_pages': 1, 'leaf_pages': 11, 'overflow_pages': 2147, 'entries': 1121}
Processing oc22/is2re-total/train/data.0000.lmdb: 1121 entries
Data(pos=[118, 3], cell=[1, 3, 3], atomic_numbers=[118], natoms=118, fixed=[118], tags=[118], nads=0, y_relaxed=-603.00763846, pos_relaxed=[118, 3], sid=79976, id='0_0', oc22=1)
Data(pos=[112, 3], cell=[1, 3, 3], atomic_numbers=[112], natoms=112, fixed=[112], tags=[112], nads=0, y_relaxed=-576.66065891, pos_relaxed=[112, 3], sid=83741, id='0_1', oc22=1)
Data(pos=[46, 3], cell=[1, 3, 3], atomic_numbers=[46], natoms=46, fixed=[46], tags=[46], nads=0, y_relaxed=-256.74895213, pos_relaxed=[46, 3], sid=45992, id='0_10', oc22=1)
Data(pos=[114, 3], cell=[1, 3, 3], atomic_numbers=[114], natoms=114, fixed=[114], tags=[114], nads=2, y_relaxed=-890.71960009, pos_relaxed=[114, 3], sid=75256, id='0_100', oc22=1)
Data(pos=[82, 3], cell=[1, 3, 3], atomic_numbers=[82], natoms=82, fixed=[82], tags=[82], nads=2, y_relaxe

In [47]:
def filter_dataset(df):
    # mask for rows with 1 H ads
    contains_h = (df['ads_symbols'] == 'H') & (df['nads'] == 1)

    # mask for rows with no adsorbates, courtesy of Claude
    def _no_ads(x):
        # None or NaN
        if pd.isna(x):
            return True
        
        # actual empty list/tuple/set
        if isinstance(x, (list, tuple, set)):
            return len(x) == 0
        
        # string forms: '', '[]', , 'None'
        s = str(x).strip()
        if s == '' or s == '[]' or s.lower() == 'none':
            return True
        
        return False

    # mask for rows with no ads
    contains_no_ads = df['ads_symbols'].apply(_no_ads)

    h = df[contains_h]
    h = h.reset_index(drop=True)

    no_ads = df[contains_no_ads]
    no_ads = no_ads.reset_index(drop=True)

    return h, no_ads

train_h, train_no_ads = filter_dataset(train)
val_id_h, val_id_no_ads = filter_dataset(val_id)
val_ood_h, val_ood_no_ads = filter_dataset(val_ood)

train_h.to_csv("data/train_h.csv", index=False)
train_no_ads.to_csv("data/train_no_ads.csv", index=False)

val_id_h.to_csv("data/val_id_h.csv", index=False)
val_id_no_ads.to_csv("data/val_id_no_ads.csv", index=False)

val_ood_h.to_csv("data/val_ood_h.csv", index=False)
val_ood_no_ads.to_csv("data/val_ood_no_ads.csv", index=False)

# sample a small subset from the full dataset
# for the purpose of featurization testing

n_samples = 100
train_h_sample = train_h.sample(n_samples)
train_no_ads_sample = train_no_ads.sample(n_samples)

train_h_sample.to_csv("data/train_h_sample.csv", index=False)
train_no_ads_sample.to_csv("data/train_no_ads_sample.csv", index=False)

print(f"size of whole training dataset: {train.shape}")
print(f"size of h-ads training dataset: {train_h.shape}")
print(f"size of no-ads training dataset: {train_no_ads.shape}")

print(f"size of whole validation (in-distribution) dataset: {val_id.shape}")
print(f"size of h-ads val id dataset: {val_id_h.shape}")
print(f"size of no-ads val id dataset: {val_id_no_ads.shape}")

print(f"size of whole validatio (out-of-distribution) dataset: {val_ood.shape}")
print(f"size of h-ads val ood dataset: {val_ood_h.shape}")
print(f"size of no-ads val ood dataset: {val_ood_no_ads.shape}")

size of whole training dataset: (45890, 9)
size of h-ads training dataset: (1605, 9)
size of no-ads training dataset: (14646, 9)
size of whole validation (in-distribution) dataset: (2624, 9)
size of h-ads val id dataset: (99, 9)
size of no-ads val id dataset: (923, 9)
size of whole validatio (out-of-distribution) dataset: (2780, 9)
size of h-ads val ood dataset: (86, 9)
size of no-ads val ood dataset: (918, 9)


## Featurization

In [49]:
# convert bulk symbols to Composition object
from pymatgen.core import Composition


pd.options.mode.copy_on_write = True

def convert_bulk_symbols(df):
    converted = df[['bulk_id', 'bulk_symbols', 'y_relaxed']]
    converted['bulk_symbols'] = converted['bulk_symbols'].apply(Composition)
    return converted

train_h = convert_bulk_symbols(train_h)
train_no_ads = convert_bulk_symbols(train_no_ads)

val_id_h = convert_bulk_symbols(val_id_h)
val_id_no_ads = convert_bulk_symbols(val_id_no_ads)

val_ood_h = convert_bulk_symbols(val_ood_h)
val_ood_no_ads = convert_bulk_symbols(val_ood_no_ads)

In [ ]:
from matminer.featurizers.composition import ElementProperty
from matminer.featurizers.composition import Stoichiometry
from matminer.featurizers.composition import ValenceOrbital
from matminer.featurizers.composition import TMetalFraction
from matminer.featurizers.composition import BandCenter
from matminer.featurizers.composition import AtomicOrbitals

from dotenv import load_dotenv
import warnings


# suppress annoying warnings
warnings.filterwarnings('ignore', message='.*impute_nan.*')

# make sure to have your materials project api in the .env file
load_dotenv()
key = os.getenv('API_KEY')

def featurize_composition(df):
    featurized_df = df.copy()
    print("Initial df shape:", featurized_df.shape)
    
    featurizers = [
        ElementProperty.from_preset("magpie"),
        Stoichiometry(),
        ValenceOrbital(),
        TMetalFraction(),
        BandCenter(),
        AtomicOrbitals(),
    ]

    for featurizer in featurizers:
        # featurizer.set_n_jobs(1)
        featurized_df = featurizer.featurize_dataframe(featurized_df, 'bulk_symbols')
    
    return featurized_df

In [ ]:
# train_h_comp_featurized = featurize_composition(train_h)
# train_no_ads_comp_featurized = featurize_composition(train_no_ads)
# train_h_comp_featurized.to_csv("data/train_h_comp_featurized.csv", index=False)
# train_no_ads_comp_featurized.to_csv("data/train_no_ads_comp_featurized.csv", index=False)

val_id_h_comp_featurized = featurize_composition(val_id_h)
val_id_no_ads_comp_featurized = featurize_composition(val_id_no_ads)
val_id_h_comp_featurized.to_csv("data/val_id_h_comp_featurized.csv", index=False)
val_id_no_ads_comp_featurized.to_csv("data/val_id_no_ads_comp_featurized.csv", index=False)

val_ood_h_comp_featurized = featurize_composition(val_ood_h)
val_ood_no_ads_comp_featurized = featurize_composition(val_ood_no_ads)
val_ood_h_comp_featurized.to_csv("data/val_ood_h_comp_featurized.csv", index=False)
val_ood_no_ads_comp_featurized.to_csv("data/val_ood_no_ads_comp_featurized.csv", index=False)

possible MP fields that can be requested by API:

['builder_meta',
 'nsites',
 'elements',
 'nelements',
 'composition',
 'composition_reduced',
 'formula_pretty',
 'formula_anonymous',
 'chemsys',
 'volume',
 'density',
 'density_atomic',
 'symmetry',
 'deprecated',
 'deprecation_reasons',
 'last_updated',
 'origins',
 'warnings',
 'property_name',
 'task_ids',
 'uncorrected_energy_per_atom',
 'formation_energy_per_atom',
 'energy_above_hull',
 'is_stable',
 'equilibrium_reaction_energy_per_atom',
 'decomposes_to',
 'xas',
 'grain_boundaries',
 'band_gap',
 'cbm',
 'vbm',
 'efermi',
 'is_gap_direct',
 'is_metal',
 'es_source_calc_id',
 'bandstructure',
 'dos',
 'dos_energy_up',
 'dos_energy_down',
 'is_magnetic',
 'ordering',
 'total_magnetization',
 'total_magnetization_normalized_vol',
 'total_magnetization_normalized_formula_units',
 'num_magnetic_sites',
 'num_unique_magnetic_sites',
 'types_of_magnetic_species',
 'bulk_modulus',
 'shear_modulus',
 'universal_anisotropy',
 'homogeneous_poisson',
 'e_total',
 'e_ionic',
 'e_electronic',
 'n',
 'e_ij_max',
 'weighted_surface_energy_EV_PER_ANG2',
 'weighted_surface_energy',
 'weighted_work_function',
 'surface_anisotropy',
 'shape_factor',
 'has_reconstructed',
 'possible_species',
 'has_props',
 'theoretical',
 'database_IDs']

DensityFeatures:
- density
- vpa
- packing fraction

GlobalSymmetryFeatures:
- spacegroup_num
- crystal_system
- crystal_system_int
- is_centrosymmetric
- n_symmetry_ops

In [52]:
# get structure properties
from mp_api.client import MPRester


def fetch_structure(df):
    structures = []
    bulk_symbols_col = df['bulk_symbols']

    with MPRester(key) as mpr:
        for row in bulk_symbols_col:
            formula = row.reduced_formula

            try:
                # retrieve SummaryDoc
                docs = mpr.materials.summary.search(
                    formula=formula,
                    fields=['structure', 'energy_per_atom']
                )
                if docs:
                    best_doc = min(docs, key=lambda x: x.energy_per_atom)
                    best_structure = best_doc.structure
                    structures.append(best_structure)
                else:
                    structures.append(None)
                    print(f"unable to get structure for {formula}")
            except:
                structures.append(None)
                print(f"cannot unable to communicate with MP REST API: {formula}")
    
    result_df = df.copy().drop(columns=['bulk_id', 'y_relaxed'])
    result_df['structure'] = structures
    return result_df

In [ ]:
# train_h_structures = fetch_structure(train_h)
# train_no_ads_structures = fetch_structure(train_no_ads)
# train_h_structures.to_csv("data/train_h_structures.csv", index=False)
# train_no_ads_structures.to_csv("data/train_no_ads_structures.csv", index=False)

val_id_h_structures = fetch_structure(val_id_h)
val_id_no_ads_structures = fetch_structure(val_id_no_ads)
val_id_h_structures.to_csv("data/val_id_h_structures.csv", index=False)
val_id_no_ads_structures.to_csv("data/val_id_no_ads_structures.csv", index=False)

val_ood_h_structures = fetch_structure(val_ood_h)
val_ood_no_ads_structures = fetch_structure(val_ood_no_ads)
val_ood_h_structures.to_csv("data/val_ood_h_structures.csv", index=False)
val_ood_no_ads_structures.to_csv("data/val_ood_no_ads_structures.csv", index=False)

In [54]:
from matminer.featurizers.structure import DensityFeatures 
from matminer.featurizers.structure import GlobalSymmetryFeatures
from matminer.featurizers.structure import SiteStatsFingerprint
from matminer.featurizers.structure import StructuralHeterogeneity
from matminer.featurizers.structure import MaximumPackingEfficiency
from matminer.featurizers.structure import ChemicalOrdering
from matminer.featurizers.structure import CoulombMatrix


def featurize_structure(df):
    featurized_df = df.copy()
    
    featurizers = [
        DensityFeatures(),
        GlobalSymmetryFeatures(),
        SiteStatsFingerprint.from_preset("LocalPropertyDifference_ward-prb-2017"),
        StructuralHeterogeneity(),
        MaximumPackingEfficiency(),
        ChemicalOrdering(),
    ]
    
    for featurizer in featurizers:
        # featurizer.set_n_jobs(1)
        featurized_df = featurizer.featurize_dataframe(
            featurized_df, 
            'structure', 
            ignore_errors=True
        )

    coulomb_matrix = CoulombMatrix(flatten=True)
    coulomb_matrix.fit(featurized_df['structure'].dropna().tolist())
    
    # coulomb_matrix.set_n_jobs(1)
    featurized_df = coulomb_matrix.featurize_dataframe(
        featurized_df,
        'structure',
        ignore_errors=True
    )
    
    return featurized_df

In [55]:
# train_h_struct_featurized = featurize_structure(train_h_structures)
# train_no_ads_struct_featurized = featurize_structure(train_no_ads_structures)
# train_h_struct_featurized.to_csv("data/train_h_struct_featurized.csv", index=False)
# train_no_ads_struct_featurized.to_csv("data/train_no_ads_struct_featurized.csv", index=False)

val_id_h_struct_featurized = featurize_structure(val_id_h_structures)
val_id_no_ads_struct_featurized = featurize_structure(val_id_no_ads_structures)
val_id_h_struct_featurized.to_csv("data/val_id_h_struct_featurized.csv", index=False)
val_id_no_ads_struct_featurized.to_csv("data/val_id_no_ads_struct_featurized.csv", index=False)

val_ood_h_struct_featurized = featurize_structure(val_ood_h_structures)
val_ood_no_ads_struct_featurized = featurize_structure(val_ood_no_ads_structures)
val_ood_h_struct_featurized.to_csv("data/val_ood_h_struct_featurized.csv", index=False)
val_ood_no_ads_struct_featurized.to_csv("data/val_ood_no_ads_struct_featurized.csv", index=False)

DensityFeatures:   0%|          | 0/99 [00:00<?, ?it/s]

GlobalSymmetryFeatures:   0%|          | 0/99 [00:00<?, ?it/s]

SiteStatsFingerprint:   0%|          | 0/99 [00:00<?, ?it/s]

StructuralHeterogeneity:   0%|          | 0/99 [00:00<?, ?it/s]

MaximumPackingEfficiency:   0%|          | 0/99 [00:00<?, ?it/s]

...

StructuralHeterogeneity:   0%|          | 0/918 [00:00<?, ?it/s]

MaximumPackingEfficiency:   0%|          | 0/918 [00:00<?, ?it/s]

ChemicalOrdering:   0%|          | 0/918 [00:00<?, ?it/s]

CoulombMatrix:   0%|          | 0/918 [00:00<?, ?it/s]

/Users/hliu/miniconda3/envs/ocp/lib/python3.12/site-packages/matminer/featurizers/structure/matrix.py:100: ComplexWarning: Casting complex values to real discards the imaginary part
  zeros[: len(eigs)] = eigs
/Users/hliu/miniconda3/envs/ocp/lib/python3.12/site-packages/matminer/featurizers/structure/matrix.py:100: ComplexWarning: Casting complex values to real discards the imaginary part
  zeros[: len(eigs)] = eigs
/Users/hliu/miniconda3/envs/ocp/lib/python3.12/site-packages/matminer/featurizers/structure/matrix.py:100: ComplexWarning: Casting complex values to real discards the imaginary part
  zeros[: len(eigs)] = eigs
/Users/hliu/miniconda3/envs/ocp/lib/python3.12/site-packages/matminer/featurizers/structure/matrix.py:100: ComplexWarning: Casting complex values to real discards the imaginary part
  zeros[: len(eigs)] = eigs
/Users/hliu/miniconda3/envs/ocp/lib/python3.12/site-packages/matminer/featurizers/structure/matrix.py:100: ComplexWarning: Casting complex values to real discar

In [56]:
# combine composition and structure features
def merge_df(comp_df, struct_df):
    return pd.concat([comp_df.set_index('bulk_symbols'),
                      struct_df.set_index('bulk_symbols')], 
                      axis=1)

# train_h_final = merge_df(train_h_comp_featurized, train_h_struct_featurized)
# train_no_ads_final = merge_df(train_no_ads_comp_featurized, train__struct_featurized)
# train_h_final.to_csv("data/train_h_final.csv")
# train_no_ads_final.to_csv("data/train_no_ads_final.csv")

val_id_h_final = merge_df(val_id_h_comp_featurized, val_id_h_struct_featurized)
val_id_no_ads_final = merge_df(val_id_no_ads_comp_featurized, val_id_no_ads_struct_featurized)
val_id_h_final.to_csv("data/val_id_h_final.csv", index=False)
val_id_no_ads_final.to_csv("data/val_id_no_ads_final.csv", index=False)

val_ood_h_final = merge_df(val_ood_h_comp_featurized, val_ood_h_struct_featurized)
val_ood_no_ads_final = merge_df(val_ood_no_ads_comp_featurized, val_ood_no_ads_struct_featurized)
val_ood_h_final.to_csv("data/val_ood_h_final.csv", index=False)
val_ood_no_ads_final.to_csv("data/val_ood_no_ads_final.csv", index=False)

# print(f"final featurized training h dataset: {train_h_final.shape}")
# print(f"final featurized training no-ads dataset: {train_no_ads_final.shape}")
print(f"final featurized val id h dataset: {val_id_h_final.shape}")
print(f"final featurized val id no-ads dataset: {val_id_no_ads_final.shape}")
print(f"final featurized val ood h dataset: {val_ood_h_final.shape}")
print(f"final featurized val ood no-ads dataset: {val_ood_no_ads_final.shape}")

final featurized val id h dataset: (99, 369)
final featurized val id no-ads dataset: (923, 469)
final featurized val ood h dataset: (86, 375)
final featurized val ood no-ads dataset: (918, 375)
